In [1]:
import torch
import torch.nn.utils.prune as prune
from ultralytics import YOLO
from copy import deepcopy

#### Tutorial for PyTorch pruning: https://towardsdatascience.com/how-to-prune-neural-networks-with-pytorch-ebef60316b91

In [2]:
def prune_model(model, amount=0.1, prune_type="unstructured", dim=0):
    """
    Prunes the model based on the specified prune_type.
    
    Args:
        model: The model to be pruned.
        amount: The amount of pruning to apply (e.g., fraction of weights to prune).
        prune_type: Type of pruning: "unstructured" or "structured".
        dim: Dimension along which to apply structured pruning (only for structured).
    
    Returns:
        model: The pruned model.
    """
    for module in model.modules():
        if isinstance(module, torch.nn.Conv2d):
            print(f"Pruning module: {module}")
            
            if prune_type == "unstructured":
                # Apply unstructured pruning
                prune.l1_unstructured(module, name="weight", amount=amount)
            elif prune_type == "structured":
                # Apply structured pruning
                prune.ln_structured(module, name="weight", amount=amount, n=2, dim=dim)
            else:
                raise ValueError(f"Unsupported prune_type: {prune_type}")
            
            # Remove the pruning mask and update the weights
            prune.remove(module, "weight")
    
    return model

In [3]:
model=YOLO("../cocoa_diseases_yolo11x_dense/train_results/weights/best.pt")
print(model.info())
torch_model=model.model

YOLO11x summary: 631 layers, 56,877,241 parameters, 0 gradients, 195.5 GFLOPs
(631, 56877241, 0, 195.46199040000002)


In [4]:
val_dense = model.val(
    data="../datasets/cocoa_diseases/cocoa_dataset.yaml",
    imgsz=640,
    batch=2,  # Small batch size
    device=[1,2]  # GPU
)

Ultralytics 8.3.58 🚀 Python-3.8.10 torch-1.13.1+cu116 CUDA:1 (NVIDIA A16, 15000MiB)
                                                       CUDA:2 (NVIDIA A16, 15000MiB)
YOLO11x summary (fused): 464 layers, 56,830,489 parameters, 0 gradients, 194.4 GFLOPs


val: Scanning /home/jovyan/ML2/datasets/cocoa_diseases/labels/val.cache... 62 images, 0 backgrounds, 0 corrupt: 100%|██████████| 62/62 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 31/31 [00:07<00:00,  4.30it/s]


                   all         62        289      0.735      0.648       0.73      0.506
          phytophthora         30         39      0.781      0.564      0.678        0.5
               monilia         23         30      0.653      0.767      0.752       0.56
               healthy         52        220      0.771      0.613       0.76      0.457
Speed: 2.1ms preprocess, 85.8ms inference, 0.0ms loss, 5.2ms postprocess per image
Results saved to runs/detect/val2


# Post-train pruning

## Local unstructured pruning

In [5]:
amount=[0.1,0.15,0.2]

for value in amount:
    pruned_torch_model=prune_model(deepcopy(torch_model),prune_type='unstructured', amount=value)
#    print(pruned_torch_model.info())
    print(f"Model pruned by {int(value*100)}%.")
    model.model=pruned_torch_model
    model.save(f"yolo11x_trained_pruned_local_unstructured_{int(value*100)}.pt")
    print("Model saved.")

Pruning module: Conv2d(3, 96, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
Pruning module: Conv2d(96, 192, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
Pruning module: Conv2d(192, 192, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(384, 384, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 96, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 96, kernel_size

In [2]:
sparse_model=YOLO('yolo11x_trained_pruned_local_unstructured_20.pt')
sparse_model.info()

YOLO11x summary (fused): 464 layers, 56,830,489 parameters, 0 gradients


(464, 56830489, 0, 0.0)

In [8]:
val_sparse= sparse_model.val(
    data="../datasets/cocoa_diseases/cocoa_dataset.yaml",
    imgsz=640,
    batch=2,  # Small batch size
    device=[1,2],  # GPU
    save_json=True
)

Ultralytics 8.3.58 🚀 Python-3.8.10 torch-1.13.1+cu116 CUDA:1 (NVIDIA A16, 15000MiB)
                                                       CUDA:2 (NVIDIA A16, 15000MiB)


val: Scanning /home/jovyan/ML2/datasets/cocoa_diseases/labels/val.cache... 62 images, 0 backgrounds, 0 corrupt: 100%|██████████| 62/62 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 31/31 [00:04<00:00,  7.27it/s]


                   all         62        289      0.332      0.517      0.329      0.178
          phytophthora         30         39      0.468      0.513      0.381       0.24
               monilia         23         30       0.34      0.633      0.404      0.211
               healthy         52        220      0.187      0.405      0.201      0.082
Speed: 1.3ms preprocess, 55.8ms inference, 0.0ms loss, 1.4ms postprocess per image
Saving runs/detect/val4/predictions.json...
Results saved to runs/detect/val4


In [8]:
# Iterate through named_parameters() to find the specified layer
for name, parameter in sparse_model.named_parameters():
#    if head in name:  # Check if the current parameter belongs to the specified layer
    print(f"Layer: {name}")
    print(f"Parameter: {parameter}")

Layer: model.model.0.conv.weight
Parameter: Parameter containing:
tensor([[[[-0.0000,  0.2634, -0.2605],
          [-0.0000, -0.2710,  0.2651],
          [ 0.0000,  0.0000, -0.0000]],

         [[ 0.0159,  0.1741, -0.1831],
          [-0.0128, -0.1699,  0.1786],
          [-0.0000, -0.0000, -0.0000]],

         [[ 0.0096,  0.0000, -0.0191],
          [-0.0000, -0.0000,  0.0124],
          [-0.0000, -0.0000,  0.0062]]],


        [[[-0.0000, -0.1489, -0.2388],
          [ 0.0100,  0.2496,  0.4338],
          [-0.0000, -0.1066, -0.1971]],

         [[ 0.0000,  0.0753,  0.0896],
          [-0.0000, -0.0843, -0.1052],
          [ 0.0000,  0.0114,  0.0225]],

         [[-0.0070,  0.0720,  0.1489],
          [-0.0000, -0.1705, -0.3325],
          [-0.0000,  0.1068,  0.1884]]],


        [[[-0.0000, -0.0000, -0.0000],
          [-0.0000,  0.0000,  0.0000],
          [-0.0000,  0.0000, -0.0000]],

         [[-0.0000,  0.0000,  0.0000],
          [ 0.0000,  0.0065,  0.0000],
          [-0.0000,

In [6]:
for name, layer in sparse_model.named_modules():
    print(layer)

YOLO(
  (model): DetectionModel(
    (model): Sequential(
      (0): Conv(
        (conv): Conv2d(3, 96, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
        (bn): BatchNorm2d(96, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
        (act): SiLU(inplace=True)
      )
      (1): Conv(
        (conv): Conv2d(96, 192, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
        (bn): BatchNorm2d(192, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
        (act): SiLU(inplace=True)
      )
      (2): C3k2(
        (cv1): Conv(
          (conv): Conv2d(192, 192, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn): BatchNorm2d(192, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
          (act): SiLU(inplace=True)
        )
        (cv2): Conv(
          (conv): Conv2d(384, 384, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn): BatchNorm2d(384, eps=0.001, momentum=0.03, affine=True, track_

## Local structured pruning

### Channel-wise

In [21]:
amount=[0.1,0.15,0.2]

for value in amount:
    pruned_torch_model=prune_model(deepcopy(torch_model), prune_type='structured', dim=0, amount=value)
#    print(pruned_torch_model.info())
    print(f"Model pruned by {int(value*100)}%.")
    model.model=pruned_torch_model
    model.save(f"yolo11x_trained_pruned_local_structured_{int(value*100)}_channel.pt")
    print("Model saved.")


Pruning module: Conv2d(3, 96, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
Pruning module: Conv2d(96, 192, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
Pruning module: Conv2d(192, 192, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(384, 384, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 96, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1))
Pruning module: Conv2d(96, 96, kernel_size

In [9]:
sparse_model=YOLO('yolo11x_trained_pruned_local_structured_10_channel.pt')

In [10]:
val_sparse= sparse_model.val(
    data="../datasets/cocoa_diseases/cocoa_dataset.yaml",
    imgsz=640,
    batch=2,  # Small batch size
    device=[1,2]  # GPU
)

Ultralytics 8.3.58 🚀 Python-3.8.10 torch-1.13.1+cu116 CUDA:1 (NVIDIA A16, 15000MiB)
                                                       CUDA:2 (NVIDIA A16, 15000MiB)


val: Scanning /home/jovyan/ML2/datasets/cocoa_diseases/labels/val.cache... 62 images, 0 backgrounds, 0 corrupt: 100%|██████████| 62/62 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 31/31 [00:03<00:00,  8.05it/s]

                   all         62        289          0          0          0          0


Speed: 0.9ms preprocess, 54.9ms inference, 0.0ms loss, 0.3ms postprocess per image
Results saved to runs/detect/val


In [12]:
for module in sparse_model.named_modules():
    print(module)

('', YOLO(
  (model): DetectionModel(
    (model): Sequential(
      (0): Conv(
        (conv): Conv2d(3, 96, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
        (bn): BatchNorm2d(96, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
        (act): SiLU(inplace=True)
      )
      (1): Conv(
        (conv): Conv2d(96, 192, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
        (bn): BatchNorm2d(192, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
        (act): SiLU(inplace=True)
      )
      (2): C3k2(
        (cv1): Conv(
          (conv): Conv2d(192, 192, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn): BatchNorm2d(192, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
          (act): SiLU(inplace=True)
        )
        (cv2): Conv(
          (conv): Conv2d(384, 384, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn): BatchNorm2d(384, eps=0.001, momentum=0.03, affine=True, t

In [11]:
# Iterate through named_parameters() to find the specified layer
for name, parameter in sparse_model.named_parameters():
    print(f"Layer: {name}")
    print(f"Parameter: {parameter}")

Layer: model.model.0.conv.weight
Parameter: Parameter containing:
tensor([[[[-3.5973e-03,  2.6343e-01, -2.6050e-01],
          [-4.2686e-03, -2.7100e-01,  2.6514e-01],
          [ 1.4668e-03,  5.2757e-03, -6.7806e-04]],

         [[ 1.5915e-02,  1.7407e-01, -1.8311e-01],
          [-1.2794e-02, -1.6992e-01,  1.7859e-01],
          [-5.3406e-04, -1.0529e-03, -3.5477e-04]],

         [[ 9.5596e-03,  2.7428e-03, -1.9150e-02],
          [-4.1466e-03, -4.1428e-03,  1.2390e-02],
          [-3.0632e-03, -1.1597e-03,  6.1951e-03]]],


        [[[-4.5319e-03, -1.4893e-01, -2.3877e-01],
          [ 9.9640e-03,  2.4963e-01,  4.3384e-01],
          [-1.3847e-03, -1.0657e-01, -1.9714e-01]],

         [[ 3.6678e-03,  7.5317e-02,  8.9600e-02],
          [-6.0806e-03, -8.4290e-02, -1.0516e-01],
          [ 5.7640e-03,  1.1406e-02,  2.2461e-02]],

         [[-7.0076e-03,  7.1960e-02,  1.4893e-01],
          [-2.8801e-03, -1.7053e-01, -3.3252e-01],
          [-3.3913e-03,  1.0675e-01,  1.8835e-01]]],




In [56]:
# Get the iterator
parameters_iterator = sparse_model.named_parameters()

# Get the first element
first_element = next(parameters_iterator)

# Get the second element
second_element = next(parameters_iterator)

third_element = next(parameters_iterator)

fourth_element = next(parameters_iterator)

# Print the first element
print(first_element[1][95])


tensor([[[-0.0780, -0.2236, -0.0407],
         [ 0.0089,  0.0428,  0.0004],
         [ 0.0623,  0.1849,  0.0510]],

        [[-0.0639, -0.1960, -0.0147],
         [ 0.0203,  0.0297, -0.0023],
         [ 0.0315,  0.1685,  0.0239]],

        [[-0.0637, -0.1753, -0.0213],
         [ 0.0207,  0.0029, -0.0082],
         [ 0.0273,  0.1600,  0.0260]]])


### Neuron-wise

In [11]:
amount=[0.1,0.15,0.2]

for value in amount:
    pruned_torch_model=prune_model(torch_model, prune_type='structured', dim=1, amount=value)
#    print(pruned_torch_model.info())
    print(f"Model pruned by {int(value*100)}%.")
    model.model=pruned_torch_model
    model.save(f"yolo11x_trained_pruned_local_structured_{int(value*100)}_neuron.pt")
    print("Model saved.")


Pruning module: Conv2d(3, 96, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
Pruning module: Conv2d(96, 192, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
Pruning module: Conv2d(192, 192, kernel_size=(1, 1), stride=(1, 1), bias=False)
Pruning module: Conv2d(384, 384, kernel_size=(1, 1), stride=(1, 1), bias=False)
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1), bias=False)
Pruning module: Conv2d(96, 48, kernel_size=(1, 1), stride=(1, 1), bias=False)
Pruning module: Conv2d(96, 96, kernel_size=(1, 1), stride=(1, 1), bias=False)
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
Pruning module: Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
Pruning module: Conv2d(96, 48, kernel_size

In [12]:
sparse_model=YOLO('yolo11x_trained_pruned_local_structured_10_neuron.pt')

In [13]:

val_sparse= sparse_model.val(
    data="../datasets/cocoa_diseases/cocoa_dataset.yaml",
    imgsz=640,
    batch=2,  # Small batch size
    device=[0,1]  # GPU
)

Ultralytics 8.3.58 🚀 Python-3.8.10 torch-1.13.1+cu116 CUDA:0 (NVIDIA A16, 15000MiB)
                                                       CUDA:1 (NVIDIA A16, 15000MiB)
YOLO11x summary (fused): 464 layers, 56,830,489 parameters, 0 gradients, 194.4 GFLOPs


val: Scanning /home/jovyan/ML2/datasets/cocoa_diseases/labels/val.cache... 62 images, 0 backgrounds, 0 corrupt: 100%|██████████| 62/62 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 31/31 [00:04<00:00,  7.56it/s]


                   all         62        289   0.000433    0.00758   0.000226   6.68e-05
          phytophthora         30         39          0          0          0          0
               monilia         23         30          0          0          0          0
               healthy         52        220     0.0013     0.0227   0.000678     0.0002
Speed: 1.1ms preprocess, 54.8ms inference, 0.0ms loss, 1.8ms postprocess per image
Results saved to runs/detect/val11


In [34]:
# Get the iterator
parameters_iterator = sparse_model.named_parameters()

# Get the first element
first_element = next(parameters_iterator)

# Print the first element
print(first_element[1][64])


tensor([[[-0.0075,  0.0059, -0.0058],
         [-0.0018, -0.0078,  0.0051],
         [ 0.0023,  0.0023,  0.0027]],

        [[-0.0088, -0.0207,  0.0019],
         [-0.0383, -0.0716, -0.0295],
         [-0.0493, -0.0740, -0.0385]],

        [[ 0.0000,  0.0000, -0.0000],
         [ 0.0000,  0.0000,  0.0000],
         [ 0.0000,  0.0000,  0.0000]]])


# Pre-train pruning

Idea is to take the base yolo11x model, prune it and then train the pruned model on the cocoa dataset